# LIBRARIES


In [1]:
# LIBRARIES #

import numpy as np
import pydicom as dcm

import datetime
from os.path import basename

from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import LinearColorMapper, BasicTicker, ColorBar, Plot, CustomJS, ColumnDataSource, Rect
from bokeh.layouts import row, gridplot, column
from bokeh.models.widgets import Slider

output_notebook()


Loading BokehJS ...

# VARIABLES

In [2]:
# INPUT VARIABLES #

FILEPATH = "imgs\\"
FILENAME = "dicom\SPECT_Jaszczak3SpheresChaudesFroides.DCM"

Ainj = 370 #MBq
Tinj = datetime.datetime(2020,2,17,16,0,0)

Ares = 7 #MBq
Tres = datetime.datetime(2020,2,17,16,5,0)

# CSTES #
T1DEMI_Tc99m = 6.0058
T1DEMI_I123 = 13.22
T1DEMI_I131 = 192.48

NB_DETECTORS = 2       # valeur fausse dans dicom header (reconstruction?)
SCAN_ARC = 360         # valeur fausse dans dicom header
NB_ANGULAR_STEPS = 60  # valeur fausse dans dicom header
ANGULAR_STEP = 6       # valeur fausse dans dicom header

ISOTOPE_NAME = "Tc99m"
T1DEMI = T1DEMI_Tc99m # hours, half life from the isotope

VOLUME_PHANT = np.pi*10.8*10.8*18.6 # cm3 ou ml pour le fantome Jaszczak

CONV_FACTOR = 85.5 # cps/MBq

# Functions

In [3]:
# CONVERT DICOM TIME INFO TO DATETIME #

def convertToDatetime(date, time):
    year = int(int(date)/10000)
    month = int(int(date)/100-year*100)
    day = int(int(date)-year*10000-month*100)
    hour = int(float(time)/10000)
    minute = int(float(time)/100-hour*100)
    seconds =  int(float(time)-minute*100-hour*10000)
    return datetime.datetime(year, month, day, hour, minute, seconds)

In [4]:
# CONVERT TO SUV IMG #

def convertToSUV(img, factor, scanduration, pixdimension, injectedActivity, phantomvolume):
    # a: factor to convert pixel values to MBq/ml
    a = factor*scanduration*(pixdimension[0]*pixdimension[1]*pixdimension[2]/1000) 
    
    # b: injected activity divided by phantom volume:
    b = injectedActivity/phantomvolume
    newimg = img/a/b

    return newimg

In [5]:
# DRAWS THE IMAGE:

def drawImg(img, nbpixx, nbpixy, nbslices, plotwidth=500, titlegraph='Graph', titlebar='Counts/s'):
    # Characteristics of the image:
    _min, _max = np.amin(img), np.amax(img)

    # Displays the dose image (p1):
    color_mapper = LinearColorMapper(palette="Viridis256", low=0, high=_max)

    color_bar = ColorBar(color_mapper=color_mapper, ticker=BasicTicker(),
                     label_standoff=12, border_line_color=None, location=(0,0),
                     title=titlebar)

    p1 = figure(plot_width=int(plotwidth*1.1), plot_height=int(plotwidth*nbpixy/nbpixx), 
                    x_range=(0,nbpixx), y_range=(0,nbpixy), 
                    title=titlegraph, toolbar_location="above")

    fig1_source = ColumnDataSource(data=dict(img=[img[int(nbslices/2),:,:]], x=[0], y=[0],
                    dw=[nbpixx], dh=[nbpixy]))

    p1.image(image='img', x='x', y='y', dw='dw', dh='dh', 
                     source=fig1_source, color_mapper=color_mapper)

    p1.add_layout(color_bar, 'right')


    # callback functions:
    callback_sliderz = CustomJS(args=dict(source=fig1_source), code="""
        var f = nbSlice_slider.value;
        //console.log(f);
        var data = source.data;
        var img = data['img'][0];
        var width = data['dw'];
        var height = data['dh'];
        //console.log(img[64*128+64]);
        for (i = 0; i < width; i++) {
            for (j = 0; j < height; j++) {
                img[j*width+i] = img3D[f][j][i];
            }
        }    
        source.change.emit();
    """)


    # plotting inline:
    sliderz = Slider(start=0, end=nbslices, value=int(nbslices/2), step=1, title="Slice nb", callback=callback_sliderz)
    callback_sliderz.args["nbSlice_slider"] = sliderz

    callback_sliderz.args["img3D"] = img #ColumnDataSource()

    # Organizing the graphs:
    grid = gridplot([[p1, sliderz]])

    show(grid)

In [14]:
# WRITES THE INTERFILE TO AN INTERFILE

def writeToInterfile(filepath, filename, array, pixSize, scanDuration=1, nbOfImgs=1):
    
    # writes the array to a raw file:
    array.astype('float32').tofile(filepath + filename + '.raw')
    
    # writes the text file:
    txtfile = open(filepath+filename+".txt","w") 
  
    txtfile.write("name of data file := " + filename +  ".raw\n") 
    txtfile.write("total number of images := " + str(nbOfImgs) +  "\n") 
    txtfile.write("imagedata  byte  order :=  LITTLEENDIAN\n")
    txtfile.write("number  of  dimensions  := 3\n")
    txtfile.write("matrix  size  [1] := " + str(array.shape[0]) +  "\n")
    txtfile.write("matrix  size  [2] := " + str(array.shape[1]) +  "\n")
    txtfile.write("matrix  size  [3] := " + str(array.shape[2]) +  "\n")
    txtfile.write("number  format  := float\n")
    txtfile.write("number  of bytes  per  pixel  := 4\n")
    txtfile.write("scaling  factor (mm/pixel) [1] := " + str(pixSize[0]) +  "\n")
    txtfile.write("scaling  factor (mm/pixel) [2] := " + str(pixSize[1]) +  "\n")
    txtfile.write("scaling  factor (mm/pixel) [3] := " + str(pixSize[2]) +  "\n")
    txtfile.write("image  duration (sec) := " + str(scanDuration) +  "\n")
    
    txtfile.close() #to change file access modes 
 
    
    

# Processing

In [15]:
# READ AND GET RELEVANT INFORMATION FROM DICOM FILE #

# reads the dicom file:
ds = dcm.read_file(FILEPATH+FILENAME)

# gets info:
patient_name = ds.PatientName

study_date = ds.StudyDate
scan_time = ds[0x0008,0x0032].value
acq_datetime = convertToDatetime(study_date,scan_time)

try:
    rescaleIntercept = ds[0x0028,0x1052].value
    rescaleSlope = ds[0x0028,0x1053].value
except KeyError:
    rescaleIntercept = 0
    rescaleSlope = 1
    
nb_slices = ds[0x0054,0x0081].value
nb_pixel_x = ds[0x0028,0x0011].value
nb_pixel_y = ds[0x0028,0x0010].value
nb_energy_win = ds.NumberOfEnergyWindows
pixSize = [(ds[0x0028,0x0030].value)[1], (ds[0x0028,0x0030].value)[0]]
frame_duration = int(ds[0x0054,0x0052][0][0x0018,0x1242].value/1000)
recons_corrections = ds[0x0028,0x0051].value

# disps info:
print("Patient name: ", patient_name)
print("Patient ID: ", ds[0x0020,0x0010].value)
print("File name:", basename(FILEPATH))
print(" ")
print("Injected Isotope: ", ISOTOPE_NAME, "(half life:", T1DEMI,"h)")
print("Injected activity: ", Ainj, " MBq @ ", Tinj)
print("Residual activity: ", Ares, " MBq @ ", Tres)
print(" ")
print("Scan date and time: ", acq_datetime)
print("Scan duration: ", frame_duration*NB_ANGULAR_STEPS, "s")
print("Nb of energy windows: " + str(nb_energy_win))
print("Nb of detectors: " + str(NB_DETECTORS))
print("Image size: {0} x {1} x {2}" .\
                format(nb_pixel_x, nb_pixel_y, nb_slices))
print("Pixel size", pixSize)
print("Rescale slope:", rescaleSlope)
print("Rescale intercept:", rescaleIntercept)
print("Rotation of detectors: ", SCAN_ARC)
print("Angular step: ", ANGULAR_STEP, "deg")
print("Nb of steps: ", NB_ANGULAR_STEPS)
print("Step duration: ", frame_duration, "s")
print("reconstruction corrections:", recons_corrections)
print(" ")
print("Camera: ", ds[0x0008,0x0070].value)
print("        ", ds[0x0008,0x1010].value)
print("Collimator name: ", ds[0x0054,0x0022][0][0x0018,0x1180].value)
print("Collimator type: ", ds[0x0054,0x0022][0][0x0018,0x1181].value)
print("Zoom factor: ", ds[0x0054,0x0022][0][0x0028,0x0031].value)

# reads the image and converts it to SUV
pixarray = ds.pixel_array[:,:,:].astype(np.float32) * rescaleSlope + rescaleIntercept


Patient name:  ZZZASMA_JASZCZAK^JASZCZAK TC99M
Patient ID:  OS 3 TEMPS
File name: 
 
Injected Isotope:  Tc99m (half life: 6.0058 h)
Injected activity:  370  MBq @  2020-02-17 16:00:00
Residual activity:  7  MBq @  2020-02-17 16:05:00
 
Scan date and time:  2020-02-17 17:41:58
Scan duration:  1200 s
Nb of energy windows: 2
Nb of detectors: 2
Image size: 128 x 128 x 120
Pixel size ["4.418156", "4.418156"]
Rescale slope: 1
Rescale intercept: 0
Rotation of detectors:  360
Angular step:  6 deg
Nb of steps:  60
Step duration:  20 s
reconstruction corrections: ['COR', 'NRGY', 'LIN', 'UNIF']
 
Camera:  GE MEDICAL SYSTEMS
         Discovery NM/CT
Collimator name:  LEHR
Collimator type:  PARA
Zoom factor:  ['1.000000', '1.000000']


In [8]:
# PLOTS IMAGE AND PROFILES #


# img corrigée du diffusé:
m_img = pixarray[0:60,:,:] - pixarray[60:120,:,:]

nb_slices = NB_ANGULAR_STEPS

drawImg(m_img, nb_pixel_x, nb_pixel_y, nb_slices, titlegraph='Projections')

# sinogram:
sinogram = np.moveaxis(m_img, [0,1,2], [1,0,2])
drawImg(sinogram, nb_pixel_x, nb_slices, nb_pixel_y, titlegraph='Sinogram')


In [17]:
# writing the information in interfile format to be able to read it in CASTOR:

array = sinogram
pixSize = (pixSize[0],pixSize[1], pixSize[1])

writeToInterfile(FILEPATH + "interfile\\", "sg", array, pixSize)

